In [1]:
import numpy as np
import pandas as pd
import cufflinks
import json
import os
from copy import deepcopy
from datetime import datetime

import trading_gym
from trading_gym.ray.logger import calculate_tearsheet, CustomLogger, PPOTensorboard
from trading_gym.registry.gaia.v7.env import GAIAPredictorsContinuousV7
from trading_gym.ray.models import MultiLayersPerceptron

import ray
from ray import rllib
from ray import tune
from ray.rllib.models import ModelCatalog
from ray.rllib.models.model import Model
from ray.rllib.models.misc import normc_initializer, get_activation_fn
from ray import cloudpickle
from ray.utils import binary_to_hex, hex_to_binary

import tensorflow as tf
import tensorflow.contrib.slim as slim

ModelCatalog.register_custom_model(MultiLayersPerceptron.__name__, MultiLayersPerceptron)
cufflinks.go_offline()
ray.init()

2019-05-24 13:49:12,647	INFO node.py:497 -- Process STDOUT and STDERR is being redirected to /tmp/ray/session_2019-05-24_13-49-12_647671_16842/logs.
2019-05-24 13:49:12,759	INFO services.py:409 -- Waiting for redis server at 127.0.0.1:25252 to respond...
2019-05-24 13:49:12,892	INFO services.py:409 -- Waiting for redis server at 127.0.0.1:14479 to respond...
2019-05-24 13:49:12,894	INFO services.py:806 -- Starting Redis shard with 6.72 GB max memory.
2019-05-24 13:49:12,932	INFO node.py:511 -- Process STDOUT and STDERR is being redirected to /tmp/ray/session_2019-05-24_13-49-12_647671_16842/logs.
2019-05-24 13:49:12,934	INFO services.py:1441 -- Starting the Plasma object store with 10.08 GB memory using /dev/shm.


{'node_ip_address': '192.168.81.206',
 'redis_address': '192.168.81.206:25252',
 'object_store_address': '/tmp/ray/session_2019-05-24_13-49-12_647671_16842/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2019-05-24_13-49-12_647671_16842/sockets/raylet',
 'webui_url': None,
 'session_dir': '/tmp/ray/session_2019-05-24_13-49-12_647671_16842'}

In [2]:
class MLP(Model):
    def _build_layers_v2(self, input_dict: dict, num_outputs: int, config: dict):
        import tensorflow.contrib.slim as slim

        with tf.name_scope("fc_net"):
            last_layer = input_dict['obs']
            activation = get_activation_fn(config.get("fcnet_activation"))
            for i, size in enumerate(config.get("fcnet_hiddens"), 1):
                last_layer = slim.fully_connected(
                    inputs=last_layer,
                    num_outputs=size,
                    weights_initializer=normc_initializer(1.0),
                    activation_fn=activation,
                    scope="fc{}".format(i),
                )
                last_layer = tf.layers.dropout(
                    inputs=last_layer,
                    rate=config['custom_options']["fcnet_dropout_rate"],
                    training=input_dict['is_training'],
                    name="dropout{}".format(i),
                )
            output = slim.fully_connected(
                inputs=last_layer,
                num_outputs=num_outputs,
                weights_initializer=normc_initializer(0.01),
                activation_fn=None,
                scope="fc_out",
            )
            return output, last_layer


ModelCatalog.register_custom_model(MLP.__name__, MLP)

In [3]:
def cloudpickleloads(obj):
    if isinstance(obj, dict):
        try:
            return cloudpickle.loads(hex_to_binary(obj["value"]))
        except:
            for key, value in obj.items():
                if isinstance(value, dict):
                    if sorted(value) == ['_type', 'value']:
                        obj[key] = cloudpickle.loads(hex_to_binary(value["value"]))
                    else:
                        obj[key] = cloudpickleloads(value)
                elif isinstance(value, list):
                    for i, item in enumerate(value):
                        obj[key][i] = cloudpickleloads(item)
    return obj

In [4]:
# key is year in which you want to test the agent.
paths = {
    2008: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2007/experiment_state-2019-05-22_15-07-20.json',
    2009: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2008/experiment_state-2019-05-22_15-15-54.json',
    2010: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2009/experiment_state-2019-05-22_15-24-56.json',
    2011: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2010/experiment_state-2019-05-22_15-33-26.json',
    2012: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2011/experiment_state-2019-05-22_15-42-43.json',
    2013: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2012/experiment_state-2019-05-22_15-51-15.json',
    2014: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2013/experiment_state-2019-05-22_16-00-19.json',
    2015: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2014/experiment_state-2019-05-22_16-09-55.json',
    2016: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2015/experiment_state-2019-05-22_16-18-51.json',
    2017: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2016/experiment_state-2019-05-22_16-27-36.json',
    2018: r'/home/federico/Desktop/repos/trading-gym/notebooks/registry/gaia/v7/logs/WalkForward-2017/experiment_state-2019-05-22_16-36-19.json',
}

policies = dict()
env_configs = dict()
for year, path in paths.items():
    print(year)
    with open(path) as f:
        metadata = json.load(f)
        checkpoints = metadata['checkpoints']
        runner_data = metadata['runner_data']
        stats = metadata['stats']

    for checkpoint in checkpoints:
        checkpoint = cloudpickleloads(checkpoint)
        cp = cloudpickle.loads(hex_to_binary(checkpoint['_checkpoint']))
        config = checkpoint['config']
        env_cls = config['env']
        env_config = config['env_config']
        path_restore = os.path.join(checkpoint['logdir'], cp.value)
        

    agent = rllib.agents.ppo.PPOTrainer(config, env_cls)
    agent.restore(path_restore)
    
    policies[year] = agent.get_policy()
    env_configs[year] = env_config
    
    


2019-05-24 13:49:13,277	WARNING ppo.py:171 -- FYI: By default, the value function will not share layers with the policy model ('vf_share_layers': False).


2008


2019-05-24 13:49:13,884	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)
/home/federico/Desktop/repos/trading-gym/.venv/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:

Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.

2019-05-24 13:49:15,232	INFO policy_evaluator.py:732 -- Built policy map: {'default_policy': <ray.rllib.agents.ppo.ppo_policy_graph.PPOPolicyGraph object at 0x7f7f68b46c50>}
2019-05-24 13:49:15,233	INFO policy_evaluator.py:733 -- Built preprocessor map: {'default_policy': <ray.rllib.models.preprocessors.NoPreprocessor object at 0x7f7f68b46828>}
2019-05-24 13:49:15,233	INFO policy_evaluator.py:344 -- Built filter map: {'default_policy': <ray.rllib.utils.filter.NoFilter object at 0x7f7f68b465c0>}
2019-05-24 13:49:15,318	INFO multi_gpu_optimizer.py:80 -- LocalMultiGPUOptimizer devices ['/cpu:0']
/home/federico/Des

2009


2019-05-24 13:49:19,693	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)
/home/federico/Desktop/repos/trading-gym/.venv/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:

Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.

2019-05-24 13:49:21,017	INFO policy_evaluator.py:732 -- Built policy map: {'default_policy': <ray.rllib.agents.ppo.ppo_policy_graph.PPOPolicyGraph object at 0x7f7e5c914ef0>}
2019-05-24 13:49:21,017	INFO policy_evaluator.py:733 -- Built preprocessor map: {'default_policy': <ray.rllib.models.preprocessors.NoPreprocessor object at 0x7f7e5c914ac8>}
2019-05-24 13:49:21,018	INFO policy_evaluator.py:344 -- Built filter map: {'default_policy': <ray.rllib.utils.filter.NoFilter object at 0x7f7e5c914908>}
2019-05-24 13:49:21,097	INFO multi_gpu_optimizer.py:80 -- LocalMultiGPUOptimizer devices ['/cpu:0']
/home/federico/Des

...

(pid=18235) /home/federico/Desktop/repos/trading-gym/.venv/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=18235) 
(pid=18235) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=18235) 
(pid=18237) /home/federico/Desktop/repos/trading-gym/.venv/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=18237) 
(pid=18237) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=18237) 


/home/federico/Desktop/repos/trading-gym/.venv/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:

Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.



(pid=18236) 2019-05-24 13:50:45,345	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 5 on CPU (please ignore any CUDA init errors)
(pid=18236) 2019-05-24 13:50:45.347268: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
(pid=18236) 2019-05-24 13:50:45.362329: E tensorflow/stream_executor/cuda/cuda_driver.cc:300] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
(pid=18236) 2019-05-24 13:50:45.362389: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:163] retrieving CUDA diagnostic information for host: fontana
(pid=18236) 2019-05-24 13:50:45.362398: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:170] hostname: fontana
(pid=18236) 2019-05-24 13:50:45.362458: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:194] libcuda reported version is: 390.116.0
(pid=18236) 2019-05-24 13:50:45.362488: I tensorflow/stream_executor/cuda/cuda_di

(pid=18805) 2019-05-24 13:50:50,277	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 4 on CPU (please ignore any CUDA init errors)
(pid=18805) 2019-05-24 13:50:50.288860: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
(pid=18805) 2019-05-24 13:50:50.311315: E tensorflow/stream_executor/cuda/cuda_driver.cc:300] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
(pid=18805) 2019-05-24 13:50:50.311381: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:163] retrieving CUDA diagnostic information for host: fontana
(pid=18805) 2019-05-24 13:50:50.311392: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:170] hostname: fontana
(pid=18805) 2019-05-24 13:50:50.311458: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:194] libcuda reported version is: 390.116.0
(pid=18805) 2019-05-24 13:50:50.311488: I tensorflow/stream_executor/cuda/cuda_di

(pid=18741) /home/federico/Desktop/repos/trading-gym/.venv/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=18741) 
(pid=18741) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=18741) 
(pid=18742) /home/federico/Desktop/repos/trading-gym/.venv/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning:
(pid=18742) 
(pid=18742) Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
(pid=18742) 
(pid=18736) 2019-05-24 13:51:02,185	INFO policy_evaluator.py:312 -- Creating policy evaluation worker 4 on CPU (please ignore any CUDA init errors)
(pid=18736) 2019-05-24 13:51:02.186467: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
(pid=18736) 2019-05-24 13:51:02.196452: E tensorflow/stream_executor/cuda/cuda

In [27]:
levels = list()
mappings = pd.DataFrame()
mapping_functions = dict()
for year, policy in policies.items():
    print('_______________________________________{}____________________________________________'.format(year))
    
    env_config = env_configs[year]
    env = env_cls(env_config)
    episode = env.sample_episode(
        fold='test-set',
        policy=policy,
    )
    renderer = env.render(
        benchmark=env._load_benchmark().squeeze().loc[str(year)],
        risk_free=env._load_risk_free().squeeze().loc[str(year)],
    )
    renderer.plotly_report()
    renderer.tearsheet()
    
    levels.append(renderer.level.to_frame().pct_change())
    
    
    
    actions = pd.DataFrame(episode.actions, index=episode.time, columns=env.action_space.contracts[1:])
    states = pd.DataFrame(episode.states, index=episode.time)
    mapping = states[0].to_frame('GAIA Predictor').join(actions['Russell 1000'])
    mappings = mappings.append(mapping)
    
    
    
    this_mapping = dict()
    env.reset()
    for predictor in np.linspace(-0.01, 0.01, 500):
        from trading_gym.registry.gaia.v7.env import EventGAIAPredictor
        from scipy.special import softmax
        event = EventGAIAPredictor(time=datetime.now(), equities=predictor)
        env.add_event(event)
        state = env.observation.get_values()

        _, _, info = policy.compute_single_action(state, [])
        logits = info['behaviour_logits']
        action = softmax(logits)
        target_weight_equity = action[0]
        this_mapping[predictor] = target_weight_equity
    mapping_functions[year] = this_mapping


_______________________________________2008____________________________________________


_______________________________________2009____________________________________________


_______________________________________2010____________________________________________


_______________________________________2011____________________________________________


_______________________________________2012____________________________________________


...

_______________________________________2014____________________________________________


_______________________________________2015____________________________________________


_______________________________________2016____________________________________________


_______________________________________2017____________________________________________


_______________________________________2018____________________________________________


In [29]:
daily_ret = pd.concat(levels).sort_index().fillna(0)
cumulative_performance = (1 + daily_ret).cumprod() - 1
cumulative_performance *= 100
cumulative_performance['Strategy relative to Aric-Benchmark'] = cumulative_performance['Strategy'] - cumulative_performance['Aric-Benchmark']
cumulative_performance.iplot()

In [30]:
levels = (1 + cumulative_performance / 100)
annual_rets = (levels.resample('Y').last() / levels.resample('Y').first() - 1)
annual_rets['Strategy relative to Aric-Benchmark'] = annual_rets['Strategy'] - annual_rets['Aric-Benchmark']
annual_rets.index = annual_rets.index.year
annual_rets *= 100
annual_rets.iplot(kind='bar', legend={'orientation': 'h'}, yTitle='%')

In [23]:
levels.drop('Strategy relative to Aric-Benchmark', axis='columns').tearsheet(
    benchmark=env._load_benchmark().loc['2008':].squeeze(),
    risk_free=env._load_risk_free().loc['2008':].squeeze(),
    #weights=env.broker.track_record.to_frame('weights_target').iloc[1:]
)

Strategy  Aric-Benchmark  \
Context              From                       2008-01-01      2008-01-01   
                     To                         2018-08-28      2018-08-28   
                     Years                          10.663          10.663   
                     Observations                     2771            2771   
Risk free            CAGR                       0.00736481      0.00736481   
                     From                       2008-01-01      2008-01-01   
                     To                         2018-08-28      2018-08-28   
Return               CAGR                         0.147097        0.161394   
                     CAGR over cash               0.139732         0.15403   
                     Overall return                3.32032         3.93038   
Risk                 Volatility                    0.13092       0.0974619   
                     Downside volatility          0.105428        0.070126   
                     Upside volatility           0.0902737       0.0705954   
                     Max drawdown                -0.191935      -0.0865477   
                     Martin risk                 0.0447487       0.0184664   
                     VaR 5%                     -0.0124964     -0.00907706   
                     VaR 2%                     -0.0178383       -0.013463   
                     VaR 1%                     -0.0236106      -0.0165932   
                     Expected shortfall 5%      -0.0196824      -0.0138517   
                     Expected shortfall 2%      -0.0270079      -0.0178668   
                     Expected shortfall 1%      -0.0336224      -0.0209335   
Risk-adjusted return Sharpe ratio                  1.06731         1.58041   
                     Sortino ratio                 1.32537         2.19647   
                     Calmar ratio                 0.728015         1.77971   
                     Martin ratio                0.0447487       0.0184664   
Outperformance       Benchmark              Aric-Benchmark  Aric-Benchmark   
                     From                       2008-01-01      2008-01-01   
                     To                         2018-08-28      2018-08-28   
                     CAGR over benchmark        -0.0125568      0.00174106   
                     Information ratio           -0.139494        0.253024   
                     CAPM Alpha                -0.00300712      0.00214802   
                     CAPM Beta                    0.973612        0.994949   

                                            USD 1M Deposit    Russell 1000  \
Context              From                       2008-01-01      2008-01-01   
                     To                         2018-08-28      2018-08-28   
                     Years                          10.663          10.663   
                     Observations                     2771            2771   
Risk free            CAGR                       0.00736481      0.00736481   
                     From                       2008-01-01      2008-01-01   
                     To                         2018-08-28      2018-08-28   
Return               CAGR                       0.00732137         0.08955   
                     CAGR over cash           -4.34354e-05       0.0821852   
                     Overall return              0.0808886         1.49556   
Risk                 Volatility                0.000660706        0.199054   
                     Downside volatility               NaN         0.16876   
                     Upside volatility         0.000661412        0.146861   
                     Max drawdown             -2.23344e-06       -0.534167   
                     Martin risk               4.24284e-08        0.140748   
                     VaR 5%                    4.46346e-06      -0.0190143   
                     VaR 2%                     3.9533e-06      -0.0292482   
                     VaR 1%                     3.6524e-06      -0.0392

In [10]:
mappings.sort_index().iplot(
    secondary_y='Russell 1000',
    vline=[str(year) for year in range(2008, 2019)]
)

In [45]:
pd.DataFrame(mapping_functions).iplot(title='Mapping functions trained with deep reinforcement learning', yTitle='Target weight for Russell 1000', xTitle='Standardized GAIA predictor')

# Full observation space

In [43]:
mappings.set_index('GAIA Predictor').iplot(kind='scatter', mode='markers', size=3, yTitle='Target weight for Russell 1000', xTitle='Standardized GAIA predictor')